# 데이터 수집 스케줄러 

In [ ]:
import os
import schedule
import time
import papermill
import logging

# 주피터 노트북 파일 경로
notebook_path = 'daum_news_crawling.ipynb'

# 로그 파일 설정
log_file_path = 'app.log'
logging.basicConfig(filename=log_file_path, level=logging.INFO)

# 콘솔 출력 핸들러 추가
console_handler = logging.StreamHandler()
console_handler.setLevel(logging.INFO)
logging.getLogger().addHandler(console_handler)

def run_notebook():
    try:
        start_time = time.strftime("%Y-%m-%d %H:%M:%S")
        print(f"주피터 노트북 실행을 시작합니다. 시작 시간: {start_time}")

        # 주피터 노트북 실행
        papermill.execute_notebook(
            input_path=notebook_path,
            output_path=f'output_{time.strftime("%Y%m%d%H%M%S")}.txt',
            kernel_name='python3',  # 사용할 커널 이름 지정
            log_output=True,  # 에러 로깅 활성화
            progress_bar=False  # 진행 상황 표시 활성화
        )

        end_time = time.strftime("%Y-%m-%d %H:%M:%S")
        print(f"주피터 노트북 실행이 종료되었습니다. 종료 시간: {end_time}")
    except Exception as e:
        error_message = f"에러 발생: {e}"
        print(error_message)

# 초기 실행
run_notebook()

# 매 1시간 마다 주피터 노트북 실행
schedule.every(1).hour.do(run_notebook)

# 스케줄러 시작
while True:
    schedule.run_pending()
    time.sleep(600)

# 다음뉴스 기사 데이터 수집

In [ ]:
# 카테고리1 - 페이지1 - 카테고리2 - 페이지1 ... 순차 : 카테고리 - 페이지 단위

import os
import requests
from bs4 import BeautifulSoup
from mysql.connector import connect, Error
from PIL import Image
import re
from datetime import datetime
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import json

# Declare as global variables
category_links = []
category_names = []
data = {}

headers = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/121.0.0.0 Safari/537.36'
}

# 'output_links_all.txt' 파일에서 카테고리 링크 읽기
def read_category_links(filename):
    global category_links, category_names

    with open(filename, 'r') as file:
        lines = file.readlines()

    # 기존의 category_links와 category_names를 초기화
    category_links.clear()
    category_names.clear()

    for line in lines:
        # 첫 번째 하이픈에서만 분할
        first_hyphen_index = line.find('-')
        if first_hyphen_index != -1:
            category_link = line[:first_hyphen_index].strip()
            category_name = line[first_hyphen_index + 1:].strip()

            category_links.append(category_link)
            category_names.append(category_name)

    # 딕셔너리 초기화
    data.clear()
    for category_name in category_names:
        data[category_name] = {'articles': []}

# 'output_links_all.txt' 파일에서 카테고리 링크 읽기
read_category_links('output_links_all.txt')

# MariaDB 연결 설정
db_config = {
    'host': 'localhost',
    'user': 'root',
    'password': '1234',
    'port': '3306',
    'raise_on_warnings': True,
}

# 'news' 데이터베이스 및 테이블 생성 함수
def create_news_table(cursor):
    # 'news01' 테이블이 이미 존재하는지 확인
    cursor.execute("SHOW TABLES LIKE 'news02'")
    result = cursor.fetchone()

    # 'news01' 테이블이 없으면 생성
    if not result:
        cursor.execute("""
            CREATE TABLE news01 (
                id INT AUTO_INCREMENT PRIMARY KEY,
                title VARCHAR(255) NOT NULL,
                content TEXT,
                link VARCHAR(255) NOT NULL,
                image_url VARCHAR(255),
                provided_time TIMESTAMP,
                category_id INT,
                FOREIGN KEY (category_id) REFERENCES categories(id)
            ) ENGINE=InnoDB DEFAULT CHARSET=utf8mb3 COLLATE=utf8mb3_general_ci
        """)

def create_categories_table(cursor):
    # 'categories' 테이블이 이미 존재하는지 확인
    cursor.execute("SHOW TABLES LIKE 'categories'")
    result = cursor.fetchone()

    # 'categories' 테이블이 없으면 생성
    if not result:
        cursor.execute("""
            CREATE TABLE categories (
                id INT AUTO_INCREMENT PRIMARY KEY,
                name VARCHAR(255) NOT NULL,
                link VARCHAR(255) NOT NULL
            ) ENGINE=InnoDB DEFAULT CHARSET=utf8mb3 COLLATE=utf8mb3_general_ci
        """)

def create_database(cursor):
    try:
        # 'news' 데이터베이스 확인
        cursor.execute("SHOW DATABASES LIKE 'news_final'")
        result = cursor.fetchone()

        # 'news' 데이터베이스 없으면 생성
        if not result:
            cursor.execute("CREATE DATABASE news_final")
            print("Database 'news_final' created.")

    except Error as create_db_err:
        print(f"Error creating or checking database: {create_db_err}")

    # 'news' 사용
    cursor.execute("USE news_final")

# 이미지 다운로드 및 저장 함수
def download_image(image_url):
    # 이미지 다운로드 및 저장
    if image_url and image_url != 'N/A':
        response = requests.get(image_url, headers=headers)
        if response.status_code == 200:
            # 이미지를 'images' 폴더에 저장
            valid_filename = re.sub(r'[\/:*?"<>|]', '', image_url.split("/")[-1])
            image_dir = "images"
            if not os.path.exists(image_dir):
                os.makedirs(image_dir)
            image_path = f"{image_dir}/{valid_filename}"
            with open(image_path, 'wb') as file:
                file.write(response.content)
            return image_path
    else:
        print(f"유효하지 않은 이미지 URL: {image_url}")
        return None

# 카테고리를 데이터베이스에 저장하는 함수
def save_category_to_database(cursor, category_name, category_link):
    # 카테고리가 이미 있는지 확인
    cursor.execute("SELECT id FROM categories WHERE name = %s", (category_name,))
    result = cursor.fetchone()

    # 카테고리가 없으면 삽입
    if not result:
        cursor.execute("INSERT INTO categories (name, link) VALUES (%s, %s)", (category_name, category_link))
        return cursor.lastrowid
    else:
        return result[0]

# provided_time 문자열을 timestamp로 변환하는 함수
def convert_to_timestamp(provided_time):
    if provided_time and provided_time != 'N/A':
        format_str = '%Y. %m. %d. %H:%M'
        dt = datetime.strptime(provided_time, format_str)
        return dt
    else:
        return 'N/A'

# 데이터를 데이터베이스에 저장하는 함수
def save_to_database(cursor, title, content, link, image_url, provided_time, category_name, category_link):
    cursor.execute("SELECT id FROM news01 WHERE link = %s", (link,))
    result = cursor.fetchone()

    if not result and content:  # content가 None이 아니고 비어 있지 않은 경우에만 저장
        insert_query = """
            INSERT INTO news01 (title, content, link, image_url, provided_time, category_id)
            VALUES (%s, %s, %s, %s, %s, %s)
        """
        category_id = save_category_to_database(cursor, category_name, category_link)
        provided_time_timestamp = convert_to_timestamp(provided_time)
        insert_values = (title, content, link, image_url, provided_time_timestamp, category_id)
        cursor.execute(insert_query, insert_values)
        print('기사 저장 완료:', title)
        print('\n' + '-' * 50 + '\n')
    elif not content:
        print('기사 저장 실패 (content가 없음):', title)
        print('\n' + '-' * 50 + '\n')
    else:
        print('이미 저장된 기사입니다:', title)
        print('\n' + '-' * 50 + '\n')

# 다음 뉴스 기사의 내용을 크롤링하는 함수
def crawl_daum_news_content(article_soup):
    content_paragraphs = article_soup.find_all('p', {'dmcf-ptype': 'general'})
    content_text = '\n'.join([paragraph.get_text(strip=True) for paragraph in content_paragraphs])
    return content_text

#  다음 뉴스 기사를 페이지 단위로 크롤링
def crawl_daum_news_category_pages(category_link, category_name, start_page=1):
    chrome_options = Options()
    chrome_options.add_argument('--headless')
    driver = webdriver.Chrome(options=chrome_options)

    try:
        selected_date = datetime.now()  # 현재 날짜 가져오기
        selected_date_str = selected_date.strftime("%Y%m%d")

        for page_number in range(start_page, start_page + 1):
            page_url = f"{category_link}?page={page_number}&regDate={selected_date_str}"

            # 디버깅 메시지 출력
            print(f"페이지에 접근 중: {page_url}")

            driver.get(page_url)

            if "다음뉴스" in driver.title:
                soup = BeautifulSoup(driver.page_source, 'html.parser')
                connection = connect(**db_config)
                cursor = connection.cursor()
                create_database(cursor)
                create_categories_table(cursor)
                create_news_table(cursor)
                save_category_to_database(cursor, category_name, category_link)

                article_links = soup.select('.tit_thumb > a.link_txt')

                for link in article_links:
                    article_url = link['href']
                    driver.get(article_url)
                    WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.CSS_SELECTOR, '.news_view')))

                    article_soup = BeautifulSoup(driver.page_source, 'html.parser')
                    title = article_soup.select_one('h3.tit_view')
                    title_text = title.get_text(strip=True) if title else 'N/A'
                    content_text = crawl_daum_news_content(article_soup)
                    image = article_soup.select_one('.news_view figure img')
                    image_url = image['src'] if image else 'N/A'
                    provided_time = article_soup.select_one('.num_date')
                    provided_time_text = provided_time.get_text(strip=True) if provided_time else 'N/A'
                    download_image(image_url)

                    # 데이터를 딕셔너리에 추가
                    data[category_name]['articles'].append({
                        'title': title_text,
                        'content': content_text,
                        'link': article_url,
                        'image_url': image_url,
                        'provided_time': provided_time_text,
                    })

                    # 데이터를 데이터베이스에 저장
                    save_to_database(cursor, title_text, content_text, article_url, image_url, provided_time_text, category_name, category_link)

                cursor.close()
                connection.commit()
                connection.close()
                print(f"MariaDB 연결 종료 - 페이지 {page_number}")

            else:
                print(f'페이지를 가져오지 못했습니다. 제목: {driver.title}')

    except Error as err:
        print(f"에러: {err}")

    finally:
        driver.quit()


# 크롤링 실행 
for i in range(len(category_links)):
    category_link = category_links[i]
    category_name = category_names[i]
    crawl_daum_news_category_pages(category_link, category_name)
    print(f"{category_name} 카테고리의 크롤링이 완료되었습니다.")


# 중복 및 20byte 이하 단문 제거

In [10]:

import mysql.connector
from collections import Counter
from nltk.tokenize import sent_tokenize
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import nltk
import Levenshtein
import pandas as pd

# NLTK 데이터 다운로드
nltk.download('punkt')
nltk.download('stopwords')

# MariaDB 연결 설정
db_config = {
    'host': 'localhost',
    'user': 'root',
    'password': 'asiae0307',
    'port': '3309',
    'database': 'news_final',  
    'raise_on_warnings': True,
}

# 'news02' 테이블에서 중복된 내용이거나 한 문장 이하의 단문인 레코드 찾기
def find_duplicate_records():
    try:
        connection = mysql.connector.connect(**db_config)
        cursor = connection.cursor()

        cursor.execute("SELECT * FROM news02")
        records = cursor.fetchall()

        duplicate_records = []

        for i, record in enumerate(records):
            content = record[2]  # 'news02' 테이블의 'content' 열이 3번째 열에 위치
            
            # 중복된 내용인지 확인
            for j, other_record in enumerate(records):
                if i != j and content == other_record[2]:
                    duplicate_records.append((record[0], record[2], other_record[0], other_record[2]))
                    break

        return duplicate_records

    except mysql.connector.Error as err:
        print(f"에러 발생: {err}")
        return None

    finally:
        if connection.is_connected():
            cursor.close()
            connection.close()
            print("MariaDB 연결 종료")

# 'news02' 테이블에서 20바이트 이하의 단문인 레코드 찾기
def find_short_records():
    try:
        connection = mysql.connector.connect(**db_config)
        cursor = connection.cursor()

        cursor.execute("SELECT * FROM news02")  
        records = cursor.fetchall()

        short_records = []

        for record in records:
            content = record[2]  # 'content' 열이 3번째 열에 위치

            # 20바이트 이하의 단문 레코드 체크
            if len(content) <= 20:
                short_records.append((record[0], record[1], record[2]))

        return short_records

    except mysql.connector.Error as err:
        print(f"에러 발생: {err}")
        return None

    finally:
        if connection.is_connected():
            cursor.close()
            connection.close()
            print("MariaDB 연결 종료")

# 중복된 내용인 레코드 출력
duplicate_records = find_duplicate_records()

if duplicate_records:
    print("중복된 레코드:")
    for pair in duplicate_records:
        print(f"중복 레코드: {pair[0]} / {pair[2]}")
else:
    print("중복된 레코드가 없습니다.")

# 20바이트 이하인 레코드 출력
short_records = find_short_records()

if short_records:
    print("\n20바이트 이하의 단문 레코드:")
    for record in short_records:
        print(f"단문 레코드: {record[0]} - {record[2]}")
else:
    print("\n20바이트 이하의 단문 레코드가 없습니다.")

# 중복된 내용인 레코드를 엑셀 파일에 저장
duplicate_df = pd.DataFrame(duplicate_records, columns=['News_ID_1', 'News_Content_1', 'News_ID_2', 'News_Content_2'])
duplicate_df.to_excel('duplicate_records.xlsx', index=False)

# 20바이트 이하의 단문 레코드를 엑셀 파일에 저장
short_df = pd.DataFrame(short_records, columns=['News_ID', 'News_Title', 'News_Content'])
short_df.to_excel('short_records.xlsx', index=False)



# 중복된 내용인 레코드 비교하여 하나만 남기고 삭제
def remove_duplicate_records():
    try:
        connection = mysql.connector.connect(**db_config)
        cursor = connection.cursor()

        # 중복된 레코드 찾기
        duplicate_records = find_duplicate_records()

        if duplicate_records:
            for pair in duplicate_records:
                # 중복된 레코드 중 하나만 남기고 삭제
                delete_query_news02 = f"DELETE FROM news02 WHERE id = {pair[0]}"
                cursor.execute(delete_query_news02)
                connection.commit()

            print("중복된 레코드 중 하나만 남기고 삭제 완료")
        else:
            print("중복된 레코드가 없습니다.")

    except mysql.connector.Error as err:
        print(f"에러 발생: {err}")

    finally:
        if connection.is_connected():
            cursor.close()
            connection.close()
            print("MariaDB 연결 종료")

# 단문 레코드 삭제
def remove_short_records():
    try:
        connection = mysql.connector.connect(**db_config)
        cursor = connection.cursor()

        # 단문 레코드 찾기
        short_records = find_short_records()

        if short_records:
            for record in short_records:
                # 단문 레코드 삭제
                delete_query_news02 = f"DELETE FROM news02 WHERE id = {record[0]}"
                cursor.execute(delete_query_news02)
                connection.commit()

            print("단문 레코드 모두 삭제 완료")
        else:
            print("단문 레코드가 없습니다.")

    except mysql.connector.Error as err:
        print(f"에러 발생: {err}")

    finally:
        if connection.is_connected():
            cursor.close()
            connection.close()
            print("MariaDB 연결 종료")

# 중복된 내용인 레코드 삭제
remove_duplicate_records()

# 단문 레코드 삭제
remove_short_records()




[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\ASIA\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\ASIA\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


MariaDB 연결 종료
중복된 레코드:
중복 레코드: 31 / 32
중복 레코드: 32 / 31
중복 레코드: 40 / 41
중복 레코드: 41 / 40
중복 레코드: 106 / 7513
중복 레코드: 127 / 128
중복 레코드: 128 / 127
중복 레코드: 301 / 302
중복 레코드: 302 / 301
중복 레코드: 303 / 301
중복 레코드: 318 / 320
중복 레코드: 320 / 318
중복 레코드: 395 / 1604
중복 레코드: 509 / 510
중복 레코드: 510 / 509
중복 레코드: 650 / 738
중복 레코드: 703 / 704
중복 레코드: 704 / 703
중복 레코드: 705 / 703
중복 레코드: 729 / 1890
중복 레코드: 738 / 650
중복 레코드: 753 / 754
중복 레코드: 754 / 753
중복 레코드: 755 / 753
중복 레코드: 756 / 753
중복 레코드: 757 / 753
중복 레코드: 758 / 753
중복 레코드: 759 / 753
중복 레코드: 820 / 822
중복 레코드: 821 / 823
중복 레코드: 822 / 820
중복 레코드: 823 / 821
중복 레코드: 825 / 821
중복 레코드: 826 / 821
중복 레코드: 838 / 839
중복 레코드: 839 / 838
중복 레코드: 840 / 838
중복 레코드: 841 / 1973
중복 레코드: 916 / 945
중복 레코드: 945 / 916
중복 레코드: 969 / 2108
중복 레코드: 970 / 2107
중복 레코드: 989 / 991
중복 레코드: 991 / 989
중복 레코드: 992 / 989
중복 레코드: 1172 / 3516
중복 레코드: 1289 / 1290
중복 레코드: 1290 / 1289
중복 레코드: 1291 / 1289
중복 레코드: 1292 / 1293
중복 레코드: 1293 / 1292
중복 레코드: 1294 / 1292
중복 레코드: 1295 / 1292
중복 레코드: 1

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\ASIA\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\ASIA\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


MariaDB 연결 종료
중복된 레코드 중 하나만 남기고 삭제 완료
MariaDB 연결 종료
MariaDB 연결 종료
단문 레코드 모두 삭제 완료
MariaDB 연결 종료


# 중복 뉴스 추출

In [7]:
import mysql.connector
from collections import Counter
from nltk.tokenize import sent_tokenize
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import nltk
import Levenshtein
import pandas as pd

# NLTK 데이터 다운로드
nltk.download('punkt')
nltk.download('stopwords')

# MariaDB 연결 설정
db_config = {
    'host': 'localhost',
    'user': 'root',
    'password': 'asiae0307',
    'port': '3309',
    'database': 'news_final',  # 실제 데이터베이스 이름에 맞게 수정하세요
    'raise_on_warnings': True,
}


def find_duplicate_records():
    try:
        connection = mysql.connector.connect(**db_config)
        cursor = connection.cursor()

        cursor.execute("SELECT * FROM news02")
        records = cursor.fetchall()

        duplicate_records = []

        for i, record in enumerate(records):
            content = record[2]  # 가정: 'news02' 테이블의 'content' 열이 3번째 열에 위치
            
            # 중복된 내용인지 확인
            for j, other_record in enumerate(records):
                if i != j and content == other_record[2]:
                    duplicate_records.append((record[0], record[2], other_record[0], other_record[2]))
                    break

        return duplicate_records

    except mysql.connector.Error as err:
        print(f"에러 발생: {err}")
        return None

    finally:
        if connection.is_connected():
            cursor.close()
            connection.close()
            print("MariaDB 연결 종료")

# 'news02' 테이블에서 20바이트 이하의 단문인 레코드 찾기
def find_short_records():
    try:
        connection = mysql.connector.connect(**db_config)
        cursor = connection.cursor()

        cursor.execute("SELECT * FROM news02")  
        records = cursor.fetchall()

        short_records = []

        for record in records:
            content = record[2]  # 'content' 열이 3번째 열에 위치

            # 20바이트 이하의 단문 레코드 체크
            if len(content) <= 20:
                short_records.append((record[0], record[1], record[2]))

        return short_records

    except mysql.connector.Error as err:
        print(f"에러 발생: {err}")
        return None

    finally:
        if connection.is_connected():
            cursor.close()
            connection.close()
            print("MariaDB 연결 종료")

# 중복된 내용인 레코드 출력
duplicate_records = find_duplicate_records()

if duplicate_records:
    print("중복된 레코드:")
    for pair in duplicate_records:
        print(f"중복 레코드: {pair[0]} / {pair[2]}")
else:
    print("중복된 레코드가 없습니다.")

# 20바이트 이하인 레코드 출력
short_records = find_short_records()

if short_records:
    print("\n20바이트 이하의 단문 레코드:")
    for record in short_records:
        print(f"단문 레코드: {record[0]} - {record[2]}")
else:
    print("\n20바이트 이하의 단문 레코드가 없습니다.")

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\ASIA\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\ASIA\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


MariaDB 연결 종료
중복된 레코드:
중복 레코드: 31 / 32
중복 레코드: 32 / 31
중복 레코드: 40 / 41
중복 레코드: 41 / 40
중복 레코드: 106 / 7513
중복 레코드: 127 / 128
중복 레코드: 128 / 127
중복 레코드: 301 / 302
중복 레코드: 302 / 301
중복 레코드: 303 / 301
중복 레코드: 318 / 320
중복 레코드: 320 / 318
중복 레코드: 395 / 1604
중복 레코드: 509 / 510
중복 레코드: 510 / 509
중복 레코드: 650 / 738
중복 레코드: 703 / 704
중복 레코드: 704 / 703
중복 레코드: 705 / 703
중복 레코드: 729 / 1890
중복 레코드: 738 / 650
중복 레코드: 753 / 754
중복 레코드: 754 / 753
중복 레코드: 755 / 753
중복 레코드: 756 / 753
중복 레코드: 757 / 753
중복 레코드: 758 / 753
중복 레코드: 759 / 753
중복 레코드: 820 / 822
중복 레코드: 821 / 823
중복 레코드: 822 / 820
중복 레코드: 823 / 821
중복 레코드: 825 / 821
중복 레코드: 826 / 821
중복 레코드: 838 / 839
중복 레코드: 839 / 838
중복 레코드: 840 / 838
중복 레코드: 841 / 1973
중복 레코드: 916 / 945
중복 레코드: 945 / 916
중복 레코드: 969 / 2108
중복 레코드: 970 / 2107
중복 레코드: 989 / 991
중복 레코드: 991 / 989
중복 레코드: 992 / 989
중복 레코드: 1172 / 3516
중복 레코드: 1289 / 1290
중복 레코드: 1290 / 1289
중복 레코드: 1291 / 1289
중복 레코드: 1292 / 1293
중복 레코드: 1293 / 1292
중복 레코드: 1294 / 1292
중복 레코드: 1295 / 1292
중복 레코드: 1

# 뉴스 요약

In [11]:
import mysql.connector
from collections import Counter
from nltk.tokenize import sent_tokenize
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import nltk
import pandas as pd
import jsonlines  
import re

# NLTK 데이터 다운로드
nltk.download('punkt')
nltk.download('stopwords')

# MariaDB 연결 설정
db_config = {
    'host': 'localhost',
    'user': 'root',
    'password': 'asiae0307',
    'port': '3309',
    'database': 'news_final',  # 실제 데이터베이스 이름에 맞게 수정
    'raise_on_warnings': True,
}

# 'summa_news' 테이블 생성 함수
def create_summa_news_table_if_not_exists(cursor):
    cursor.execute("SHOW TABLES LIKE 'summa_news'")
    result = cursor.fetchone()

    if not result:
        cursor.execute("""
            CREATE TABLE summa_news (
                id INT AUTO_INCREMENT PRIMARY KEY,
                news_id INT,
                summary TEXT,
                FOREIGN KEY (news_id) REFERENCES news02(id)
            ) ENGINE=InnoDB DEFAULT CHARSET=utf8mb3 COLLATE=utf8mb3_general_ci
        """)
        print("테이블 'summa_news'가 생성되었습니다.")

# 문장 중요도 계산 함수
def calculate_sentence_importance(content):
    sentences = sent_tokenize(content)
    
    stop_words = set(stopwords.words('english'))
    word_tokens = word_tokenize(content)
    filtered_words = [word.lower() for word in word_tokens if word.isalnum() and word.lower() not in stop_words]
    
    word_frequency = Counter(filtered_words)
    sentence_importance = {sentence: sum(word_frequency[word] for word in word_tokenize(sentence.lower()) if word.isalnum()) for sentence in sentences}
    
    return sentence_importance


# 뉴스 요약 및 데이터베이스에 저장 함수
def summarize_and_save_to_database(news_id, content, num_sentences=3):
    # [기자 이름 기자], (기자 이름 기자), 기자 이름 기자 패턴 찾기 및 제거
    content = re.sub(r'\[.*?\]|\(.*?\)|\s기자\s', '', content)
    
    # '기자' 다음에 나오는 글자들 제거
    content = re.sub(r'기자\s{1,2}[\wㄱ-ㅎㅏ-ㅣ가-힣]{2,5}', '기자', content)
    
    # [기자 이름 기자], (기자 이름 기자), 기자 이름 기자 패턴 찾기 및 제거
    content = re.sub(r'\[.*?(\S+)\s기자\]', r'', content)
    content = re.sub(r'\(.*?(\S+)\s기자\)', r'', content)
    content = re.sub(r'(\S+)\s기자', r'', content)



    # 이메일 주소 제거
    content = re.sub(r'\S+@\S+', '', content)

    # '사진=' 패턴 찾기 및 제거
    content = re.sub(r'사진=', '', content)

    # 특수기호(쉼표와 마침표, 작은따옴표와 큰따옴표 제외) 제거
    content = re.sub(r'[^\w\sㄱ-ㅎㅏ-ㅣ가-힣,.\'"]', '', content)
    content = re.sub(r'\n', '', content)



    try:
        connection = mysql.connector.connect(**db_config)
        cursor = connection.cursor()

        create_summa_news_table_if_not_exists(cursor)

        cursor.execute("SELECT id FROM summa_news WHERE news_id = %s", (news_id,))
        result = cursor.fetchone()

        if not result:
            sentence_importance = calculate_sentence_importance(content)
            sorted_sentences = sorted(sentence_importance, key=sentence_importance.get, reverse=True)

            summary = ' '.join(sorted_sentences[:num_sentences])

            cursor.execute("INSERT INTO summa_news (news_id, summary) VALUES (%s, %s)", (news_id, summary))
            connection.commit()
            print(f"뉴스 ID {news_id}에 대한 요약이 'summa_news' 테이블에 저장되었습니다.")
            
            print(f"뉴스 ID {news_id} 요약 내용: {summary}")

            return summary
        else:
            print(f"뉴스 ID {news_id}에 대한 요약은 이미 존재합니다.")
            return None

    except mysql.connector.Error as err:
        print(f"에러 발생: {err}")
        return None

    finally:
        if connection.is_connected():
            cursor.close()
            connection.close()
            print("MariaDB 연결 종료")

# JSONL 파일에 저장하는 함수 추가
def save_to_jsonl(original_articles, summaries, filename='news_summaries.jsonl'):
    with jsonlines.open(filename, 'w') as writer:
        for original_article, summary in zip(original_articles, summaries):
            data = {'Original Article': original_article, 'Summary': summary}
            writer.write(data)
    print(f"데이터가 '{filename}' 파일에 저장되었습니다.")

# 모든 뉴스에 대해 요약하고 'summa_news' 테이블에 저장
original_articles = []
summaries = []

try:
    connection = mysql.connector.connect(**db_config)
    cursor = connection.cursor()

    cursor.execute("SELECT id, content FROM news02")
    news_articles = cursor.fetchall()

    for article_id, article_content in news_articles:
        summary = summarize_and_save_to_database(article_id, article_content)
        
        if summary is not None:
            original_articles.append(article_content)
            summaries.append(summary)

except mysql.connector.Error as err:
    print(f"에러 발생: {err}")

finally:
    if connection.is_connected():
        cursor.close()
        connection.close()
        print("MariaDB 연결 종료")

# JSONL 파일에 저장
save_to_jsonl(original_articles, summaries)


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\ASIA\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\ASIA\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


테이블 'summa_news'가 생성되었습니다.
뉴스 ID 1에 대한 요약이 'summa_news' 테이블에 저장되었습니다.
뉴스 ID 1 요약 내용: 19일 방송된 SBS 예능 프로그램 '동상이몽 시즌2너는 내 운명'에서는 김혜선이 여동생 가족과 함께 설 명절을 보내는 모습이 전파를 탔다.이날 방송에서 김혜선은 거실에서 여동생과 함께 명절음식을 만들다 어린 시절 기억을 떠올렸다. 신문 배달부터 우유 배달, 편의점 알바, 의류 매장, 피자 가게 등등"이라며 어린 나이에 여동생을 책임지기 위해 부지런히 일했던 과거를 회상했다.그러면서 "안 해본 일 없이 대학 포기 후 공장 취업했었지 않나. 달마다 '세라 용돈' 무조건 쓰여 있고 심지어 내 휴대폰 비용까지 내줬다"며 김혜선에 고마운 마음을 전했다.스튜디오에서 VCR영상을 보던 김구라는 "예나 지금이나 일생을 퍼주는 언니다.
MariaDB 연결 종료
뉴스 ID 2에 대한 요약이 'summa_news' 테이블에 저장되었습니다.
뉴스 ID 2 요약 내용:  한국 탁구 남여 대표팀 모두 4전 전승으로 조별리그를 마무리했다.한국 남자 대표팀은 19일 오전 10시 부산 벡스코에서 열린 BNK부산은행 2024 부산세계탁구선수권대회 조별리그 3조 인도와의 마지막 경기에서 매치 스코어 30으로 승리했다.4전 4승이다. 지난 16일 폴란드와의 조별리그 첫 경기에서 31로 승리하며 쾌조의 스타트를 끊었다. 선봉장으로 나선 장우진이 마체이 쿠빅에게 연속 두 세트를 내줬지만, 내리 3세트를 따내며 웃었다. 2세트에 나온 임종훈은 밀로시 레짐스키를 상대로 31 승리를 거뒀다. 안재현이 야쿱 디아스에게 13으로 패했지만, 4세트에 다시 출전한 장우진이 레짐스키를 30으로 잡으며 경기를 마무리했다.남자 대표팀은 뉴질랜드와 두 번째 경기에서 만났다. 압도적인 기량으로 30 완승을 거뒀다. 첫 경기에 출전한 안재현이 알프데라 델라 페냐를 상대로 10으로 잡았다. 2경기는 이상수와 '한국계' 티모시 최가 맞붙었는데, 이상수가 30으로 제압했다. 

# 뉴스 태그 추출

In [ ]:

import pymysql
import pandas as pd
from sqlalchemy import create_engine
import mysql.connector
from sklearn.feature_extraction.text import TfidfVectorizer
from eunjeon import Mecab
import re
import numpy as np

# MariaDB 연결 설정
db_config = {
    'host': 'localhost',
    'user': 'root',
    'password': '1234',
    'database': 'news_final',
    'port': 3306
}

# MariaDB에 태그 테이블 생성
def create_news_tags_table(cursor):
    cursor.execute("""
        CREATE TABLE IF NOT EXISTS news_tags (
            news_id INT,
            tag VARCHAR(255) CHARACTER SET utf8 COLLATE utf8_general_ci,
            pos_tag VARCHAR(50) CHARACTER SET utf8 COLLATE utf8_general_ci
        )
    """)

# MariaDB에 전처리된 데이터 테이블 생성
def create_preprocessed_data_table(cursor):
    cursor.execute("""
        CREATE TABLE IF NOT EXISTS preprocessed_data (
            news_id INT,
            title VARCHAR(255) CHARACTER SET utf8 COLLATE utf8_general_ci,
            preprocessed_content TEXT CHARACTER SET utf8 COLLATE utf8_general_ci
        )
    """)

# MariaDB에 전처리된 데이터 삽입
def insert_preprocessed_data_to_database(cursor, news_id, title, preprocessed_content):
    cursor.execute("INSERT INTO preprocessed_data (news_id, title, preprocessed_content) VALUES (%s, %s, %s)",
                   (news_id, title, preprocessed_content))

# MariaDB에 태그 데이터 삽입
def insert_news_tags_to_database(cursor, news_id, news_tag, pos_tag):
    for tag, pos in zip(news_tag, pos_tag):
        cursor.execute("INSERT INTO news_tags (news_id, tag, pos_tag) VALUES (%s, %s, %s)", (news_id, tag, pos))

# 데이터베이스에서 뉴스 기사와 카테고리 정보 가져오기
def fetch_data_from_database():
    connection = mysql.connector.connect(**db_config)
    cursor = connection.cursor()
    query = "SELECT id, title, content FROM news02"
    cursor.execute(query)
    data = cursor.fetchall()
    connection.close()
    return data

def preprocess_text(record):
    news_id, title, content = record

    # [기자 이름 기자], (기자 이름 기자), 기자 이름 기자 패턴 찾기 및 제거
    content = re.sub(r'\[.*?\]|\(.*?\)|\s기자\s', '', content)

    # 이메일 주소 제거
    content = re.sub(r'\S+@\S+', '', content)

    # '사진=' 패턴 찾기 및 제거
    content = re.sub(r'사진=', '', content)

    # 특수기호 제거
    content = re.sub(r'[^\w\sㄱ-ㅎㅏ-ㅣ가-힣]', '', content)
    
    # 소문자 변환
    content = re.sub(r'[A-Z]', lambda x: x.group(0).lower(), content)

    return news_id, title, content

# 불용어 처리를 위한 불용어 파일 경로
stopwords_path = 'stopwords.txt'

with open(stopwords_path, 'r', encoding='utf-8') as stopwords_file:
    stopwords = set(stopwords_file.read().splitlines())

# MeCab을 사용한 형태소 분석기 초기화
mecab = Mecab()

# 형태소 분석 함수 정의 / 토큰화 및 불용어 처리
def tokenize(text):
    nodes = mecab.pos(text)
    result = []
    for node in nodes:
        if node[1].split(',')[0] in ['NNG', 'NNP', 'VV', 'VA', 'VX', 'MAG'] and node[0] not in stopwords:
            result.append(node[0])
    return result

# TF-IDF Vectorizer 정의
tfidf_vectorizer = TfidfVectorizer(tokenizer=tokenize, max_features=1000)  # 상위 1000개의 단어만 사용

# 데이터를 문장으로 분리
train_data = fetch_data_from_database()

print(train_data)

# 예시: 모든 뉴스에 대해 태그 추출 및 데이터베이스 저장
connection = mysql.connector.connect(**db_config)
cursor = connection.cursor()

create_news_tags_table(cursor)
create_preprocessed_data_table(cursor)

# 모든 문서를 통해 TF-IDF Vectorizer를 fitting
all_documents = [preprocess_text(record)[2] for record in train_data]
tfidf_vectorizer.fit(all_documents)

# 결과를 저장할 데이터프레임 생성
result_df = pd.DataFrame(columns=['news_id', 'title', 'preprocessed_content', 'news_tag', 'pos_tag'])

for record in train_data:
    news_id, title, content = preprocess_text(record)

    # 기사 내용에 대해 토큰화 및 전처리를 수행하여 태그 추출
    preprocessed_content = ' '.join(tokenize(content))

    # TF-IDF Vectorizer를 사용하여 문서 벡터 생성
    tfidf_vector = tfidf_vectorizer.transform([preprocessed_content])

    # 각 문서에서 가장 중요한 단어들의 인덱스를 추출
    feature_names = np.array(tfidf_vectorizer.get_feature_names_out())

    # 상위 3개의 단어만 사용하여 태그 추출
    sorted_indices = np.argsort(tfidf_vector.toarray().flatten())[::-1][:3]
    news_tag = feature_names[sorted_indices]

    # 토큰화된 문서의 품사 태그 추출
    pos_tags = [pos for _, pos in mecab.pos(preprocessed_content)]

    # 결과를 데이터프레임에 추가
    result_df = pd.concat([
        result_df,
        pd.DataFrame({
            'news_id': [news_id],
            'title': [title],
            'preprocessed_content': [preprocessed_content],
            'news_tag': [news_tag],
            'pos_tag': [pos_tags]
        })
    ], ignore_index=True)

    # 추출한 태그를 데이터베이스에 삽입
    insert_news_tags_to_database(cursor, news_id, news_tag, pos_tags)

    # 전처리된 데이터를 데이터베이스에 삽입
    insert_preprocessed_data_to_database(cursor, news_id, title, preprocessed_content)

# 결과를 엑셀 파일로 내보내기
result_df.to_excel('preprocessed_data.xlsx', index=False)

connection.commit()
connection.close()



# 사용자 정보 저장

In [ ]:
# 사용자 정보 저장

import mysql.connector

# MySQL 연결 설정
conn = mysql.connector.connect(
    host='localhost',
    user='root',
    password='1234',
    database='news_final',
    port=3306
)

# 커서 생성
cursor = conn.cursor()

# MariaDB에 사용자 테이블 생성 또는 존재 확인
def create_user_table(cursor):
    cursor.execute("""
        CREATE TABLE IF NOT EXISTS users (  
            user_id VARCHAR(500) PRIMARY KEY,
            username VARCHAR(255),
            email VARCHAR(255) UNIQUE,
            gender VARCHAR(50),
            age INT
        ) ENGINE=InnoDB DEFAULT CHARSET=utf8mb3 COLLATE=utf8mb3_general_ci
    """)

# 테이블 생성 또는 존재 확인 함수 호출
create_user_table(cursor)

try:
    # user_data 테이블에서 user_id 값을 가져오는 SQL 쿼리
    select_query = "SELECT user_id FROM user_data"

    # 쿼리 실행
    cursor.execute(select_query)

    # 결과 가져오기
    result = cursor.fetchall()

    # users 테이블에 저장하는 SQL 쿼리 (중복 처리)
    insert_query = "INSERT INTO users (user_id) VALUES (%s) ON DUPLICATE KEY UPDATE user_id = user_id"

    # 가져온 결과를 users 테이블에 저장
    for row in result:
        cursor.execute(insert_query, row)

    # 변경사항 저장
    conn.commit()

except Exception as e:
    print(f"Error: {e}")

finally:
    # 연결 종료
    cursor.close()
    conn.close()

# 사용자 발화 Tokenize 및 저장

In [ ]:

import mysql.connector
from eunjeon import Mecab
from collections import Counter
import re

# MariaDB 연결 설정
db_config = {
    'host': 'localhost',
    'user': 'root',
    'password': '1234',
    'database': 'news_final',
    'port': 3306,
    'charset': 'utf8mb4',
    'collation': 'utf8mb3_general_ci'
}

# MeCab을 사용한 형태소 분석기 초기화
mecab = Mecab()

# 불용어 처리를 위한 불용어 파일 경로
stopwords_path = 'stopwords.txt'

# 불용어 로드
with open(stopwords_path, 'r', encoding='utf-8') as stopwords_file:
    stopwords = set(stopwords_file.read().splitlines())

# 형태소 분석 함수 정의
def tokenize(text):
    # 이메일 주소 제거
    text = re.sub(r'\S+@\S+', '', text)
    # 기자 이름 제거 (예시)
    text = re.sub(r'기자\s?\w+', '', text)
    # 특수 문자 및 숫자 제거
    text = re.sub(r'[^ㄱ-ㅎㅏ-ㅣ가-힣a-zA-Z\s]', '', text)
    
    nodes = mecab.pos(text)
    result = []
    for node in nodes:
        if node[1].split(',')[0] in ['NNG', 'NNP', 'VV', 'VA', 'VX', 'MAG'] and node[0] not in stopwords:
            result.append((node[0], node[1].split(',')[0]))  # 단어와 품사를 함께 저장
    return result

# MariaDB에 사용자 테이블 생성 또는 존재 확인
def create_user_table(cursor):
    cursor.execute("""
        CREATE TABLE IF NOT EXISTS users (  
            user_id VARCHAR(500) PRIMARY KEY,
            username VARCHAR(255) NOT NULL,
            email VARCHAR(255) UNIQUE,
            gender CHAR(1),
            age INT
        ) ENGINE=InnoDB DEFAULT CHARSET=utf8mb4 COLLATE=utf8mb3_general_ci
    """)

# MariaDB에 사용자 태그 테이블 생성 또는 존재 확인
def create_user_tags_table(cursor):
    cursor.execute("""
        CREATE TABLE IF NOT EXISTS user_tags (
            user_id VARCHAR(500),  
            user_tag VARCHAR(255) CHARACTER SET utf8mb4 COLLATE utf8mb3_general_ci,
            pos_tag VARCHAR(50),
            count INT,
            ranking INT
        ) ENGINE=InnoDB DEFAULT CHARSET=utf8mb4 COLLATE=utf8mb3_general_ci
    """)

# MariaDB에 사용자 데이터 삽입
def insert_user_to_database(cursor, user_id):
    cursor.execute("INSERT INTO users (user_id) VALUES (%s) ON DUPLICATE KEY UPDATE user_id = user_id", (user_id))
    return cursor.lastrowid  # 자동으로 증가되는 user_id를 가져옴

# MariaDB에 사용자 태그 데이터 삽입
def insert_user_tags_to_database(cursor, user_id, user_tag):
    # 기존 사용자 태그 조회
    cursor.execute("SELECT user_tag, count FROM user_tags WHERE user_id = %s", (user_id,))
    existing_tags = dict(cursor.fetchall())

    # 현재 입력에서 각 태그의 발생 횟수 카운트
    tag_counts = Counter(user_tag)

    # 기존 태그에 대한 카운트 업데이트 및 새로운 태그 추가
    for i, ((user_tag, pos_tag), count) in enumerate(tag_counts.items(), start=1):
        if user_tag in existing_tags:
            # 이미 존재하는 태그인 경우 카운트 업데이트
            existing_count = existing_tags[user_tag]
            cursor.execute("""
                UPDATE user_tags
                SET count = %s
                WHERE user_id = %s AND user_tag = %s
            """, (existing_count + count, user_id, user_tag))
        else:
            # 사용자에게 새로운 태그인 경우, 카운트 및 랭킹과 함께 삽입
            cursor.execute("""
                INSERT INTO user_tags (user_id, user_tag, pos_tag, count, ranking)
                VALUES (%s, %s, %s, %s, %s)
            """, (user_id, user_tag, pos_tag, count, i))

# 'user_data' 테이블에서 데이터 로드하고 태그 처리
def process_user_data(cursor):
    cursor.execute("SELECT user_id, utterance FROM user_data")
    user_data_rows = cursor.fetchall()

    for user_id, utterance in user_data_rows:
        user_tags = tokenize(utterance)
        insert_user_tags_to_database(cursor, user_id, user_tags)

# 데이터베이스에 연결
connection = mysql.connector.connect(**db_config)
cursor = connection.cursor()

# 테이블 생성 또는 확인
create_user_table(cursor)
create_user_tags_table(cursor)

# 사용자 데이터 처리 및 'user_tags' 테이블에 삽입
process_user_data(cursor)

# 변경 사항 커밋 및 연결 종료
connection.commit()
connection.close()

print("태그가 성공적으로 추출되어 저장되었습니다.")


# 사용자 태그 저장 및 매핑 테이블 생성

In [ ]:
# 사용자 태그 저장 및 매핑 테이블 생성

import mysql.connector
from eunjeon import Mecab
import re

# MariaDB 연결 설정
db_config = {
    'host': 'localhost',
    'user': 'root',
    'password': '1234',
    'database': 'news_final',
    'port': 3306
}

# MeCab을 사용한 형태소 분석기 초기화
mecab = Mecab()

# 불용어 처리를 위한 불용어 파일 경로
stopwords_path = 'stopwords.txt'

# 불용어 로드
with open(stopwords_path, 'r', encoding='utf-8') as stopwords_file:
    stopwords = set(stopwords_file.read().splitlines())

# 형태소 분석 함수 정의
def tokenize(text):
    # 특수 문자 및 숫자 제거
    text = re.sub(r'[^ㄱ-ㅎㅏ-ㅣ가-힣a-zA-Z\s]', '', text)
    
    nodes = mecab.pos(text)
    result = []
    for node in nodes:
        if node[1].split(',')[0] in ['NNG', 'NNP', 'VV', 'VA', 'VX', 'MAG'] and node[0] not in stopwords:
            result.append((node[0], node[1].split(',')[0]))  # 단어와 품사를 함께 저장
    return result

# MariaDB 연결
connection = mysql.connector.connect(**db_config)
cursor = connection.cursor()

def create_user_tags_table(cursor):
    cursor.execute("""
        CREATE TABLE IF NOT EXISTS user_tags (  
            tag_id INT AUTO_INCREMENT PRIMARY KEY,
            tag_name VARCHAR(255) UNIQUE
        ) ENGINE=InnoDB DEFAULT CHARSET=utf8mb3 COLLATE=utf8mb3_general_ci;
    """)
    
def create_user_tags_mapping_table(cursor):
    cursor.execute("""
        CREATE TABLE user_tags_mapping (
            user_id VARCHAR(500),
            tag_id INT,
            count INT,
            ranking INT,
            PRIMARY KEY (user_id, tag_id),
            FOREIGN KEY (user_id) REFERENCES users(user_id),
            FOREIGN KEY (tag_id) REFERENCES user_tags(tag_id) 
        ) ENGINE=InnoDB DEFAULT CHARSET=utf8mb3 COLLATE=utf8mb3_general_ci;
    """)    
create_user_tags_table(cursor)    
create_user_tags_mapping_table(cursor)  

try:
    # user_data 테이블에서 utterance 값을 가져오는 SQL 쿼리
    select_query = "SELECT user_id, utterance FROM user_data"
    cursor.execute(select_query)
    user_rows = cursor.fetchall()

    # user_tags 테이블에 저장하는 SQL 쿼리 (중복 시 업데이트)
    insert_tag_query = """
        INSERT INTO user_tags (tag_name)
        VALUES (%s)
        ON DUPLICATE KEY UPDATE tag_name=tag_name
    """

    # user_tags_mapping 테이블에 저장하는 SQL 쿼리
    insert_mapping_query = """
        INSERT INTO user_tags_mapping (user_id, tag_id, count)
        VALUES (%s, %s, %s)
        ON DUPLICATE KEY UPDATE count = count + 1
    """

    # 가져온 결과를 user_tags 테이블에 저장
    for user_row in user_rows:
        user_id, utterance = user_row
        user_tags = tokenize(utterance)

        for user_tag in user_tags:
            # user_tags 테이블에 저장
            cursor.execute(insert_tag_query, (user_tag[0],))

            # user_tags_mapping 테이블에 저장
            cursor.execute("SELECT tag_id FROM user_tags WHERE tag_name = %s", (user_tag[0],))
            tag_id = cursor.fetchone()[0]
            cursor.execute(insert_mapping_query, (user_id, tag_id, 1))

    # 변경사항 저장
    connection.commit()
    print("태그 및 매핑이 저장되었습니다.")

except Exception as e:
    print(f"Error: {e}")

finally:
    # 연결 종료
    cursor.close()
    connection.close()


# 뉴스 요약 중복 및 20byte 이하 단문 제거

# 연관 검색어 수집 저장

In [ ]:
from collections import Counter
import mysql.connector
import urllib.parse
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import time

db_config = {
    'host': 'localhost',
    'user': 'root',
    'password': '1234',
    'database': 'news_final',
    'port': 3306
}

# MariaDB 연결
conn = mysql.connector.connect(**db_config)
cursor = conn.cursor()

try:
    # 태그 데이터 추출
    cursor.execute('SELECT news_id, tag FROM news_tags') 
    tag_data = cursor.fetchall()

    for row in tag_data:
        tag_id, tags = row

        keyword = tags 
        enc_text = urllib.parse.quote(keyword)
        print(keyword)

        # 검색 결과 페이지 URL
        search_url = f"https://search.daum.net/search?w=tot&q={enc_text}&DA=V5A"

        # 웹 드라이버 설정
        driver = webdriver.Chrome()

        try:
            # 검색 결과 페이지 열기
            driver.get(search_url)

            # 대기 시간 추가
            time.sleep(3)  # 페이지 로딩 시간에 따라 지연을 조절하세요.

            # 대기 후 연관 검색어 추출
            WebDriverWait(driver, 30).until(EC.presence_of_element_located((By.CSS_SELECTOR, '#netizen_lists_top .keyword')))
            related_searches = driver.find_elements(By.CSS_SELECTOR, '#netizen_lists_top .keyword')
            related_keywords = [related_search.text for related_search in related_searches]

            # 상위 3개의 연관 검색어 가져오기
            top_related_keywords = related_keywords[:3]
            print(top_related_keywords)

            # 각 단어를 각 행으로 저장
            for keyword in top_related_keywords:
                # 데이터베이스 업데이트 쿼리 실행
                cursor.execute("INSERT INTO rs_words (tag_id, related_terms) VALUES (%s, %s)", (tag_id, keyword))
                conn.commit()

            print("검색된 키워드가 rs_words 테이블에 저장되었습니다.")

        except mysql.connector.Error as err:
            print("에러 발생:", err)

        finally:
            # 웹 드라이버 종료
            driver.quit()

except mysql.connector.Error as err:
    print("에러 발생:", err)

finally:
    # 연결 종료
    conn.close()
